Script de medición y carga de las colecciones en cluster Cassandra
TFM Daniel Herranz Segundo

In [5]:
!pip install cassandra-driver
!pip install install scales
!pip install numpy

In [6]:
import pandas as pd
import numpy as np
import os
import json
import random
from cassandra.cluster import Cluster
from cassandra.auth import PlainTextAuthProvider
import time
from pprint import pprint
import psutil
import uuid

In [7]:
def save_results_to_csv(results,file,consistencyLevel):
    #Guardamos los resultados en csv
    from datetime import datetime
    dia = datetime.now().strftime("%d%m%Y_%H_%M_%S") 
    data = results
    results_df = pd.DataFrame(data, columns =['Registros', 'Tiempo', 'CPU','Memoria'])
    results.to_csv(file.format(consistencyLevel, str(dia)))

In [8]:
resultados_etl_CutomerProfileKeySpace = '../Results/Cassandra/MongoDB_Bulk_Insert_ConsistencyLevel_{}_CustomerProfile_{}.csv'
resultados_etl_PositionKeepingKeySpace = '../Results/Cassandra/MongoDB_Bulk_Insert_ConsistencyLevel_{}_PositionKeeping_{}.csv'
resultados_etl_CurrentAccountKeySpace = '../Results/Cassandra/MongoDB_Bulk_Insert_ConsistencyLevel_{}_CurrentAccount_{}.csv'

In [9]:
#repeticiones
repeats = 1000
test_wc = False

In [10]:
from cassandra.cluster import Cluster, ExecutionProfile, EXEC_PROFILE_DEFAULT
from cassandra.policies import WhiteListRoundRobinPolicy, DowngradingConsistencyRetryPolicy
from cassandra.query import tuple_factory
from cassandra import ConsistencyLevel

profile = ExecutionProfile(
    load_balancing_policy=WhiteListRoundRobinPolicy(['127.0.0.1']),
    retry_policy=DowngradingConsistencyRetryPolicy(),
    consistency_level=ConsistencyLevel.LOCAL_QUORUM,
    serial_consistency_level=ConsistencyLevel.LOCAL_SERIAL,
    request_timeout=15,
    row_factory=tuple_factory
)
cluster = Cluster(execution_profiles={EXEC_PROFILE_DEFAULT: profile})
session = cluster.connect()
print(session.execute("SELECT release_version FROM system.local").one())

session.execute('USE customerprofilekeyspace')

rows = session.execute('SELECT * FROM customerprofile')

for row in rows:
    print(row)

('4.0.3',)


InvalidRequest: Error from server: code=2200 [Invalid query] message="Keyspace 'customerprofilekeyspace' does not exist"

## Carga de los documentos por cada dominio

In [7]:
CurrentAccountKeyspace_file_out = '../MockData/Cassandra/CurrentAccountKeyspace/CurrentAccountKeyspace.csv'
CurrentAccountKeyspaceAccountInfo_file_out = '../MockData/Cassandra/CurrentAccountKeyspace/CurrentAccountAccountInfoKeyspace.csv'
PositionKeepingKeyspace_file_out = '../MockData/Cassandra/PositionKeepingKeyspace/PositionKeepingKeyspace.csv'
CustomerProfileKeyspace_file_out = '../MockData/Cassandra/CustomerProfileKeyspace/CustomerProfileKeyspace.csv'
CustomerProfileAddressKeyspace_file_out = '../MockData/Cassandra/CustomerProfileKeyspace/CustomerProfileAddressKeyspace.csv'

CurrentAccountKeyspace_sample_out = '../MockData/Cassandra/CurrentAccountKeyspace/CurrentAccountKeyspace_sample.csv'
CurrentAccountKeyspaceAccountInfo_sample_out = '../MockData/Cassandra/CurrentAccountKeyspace/CurrentAccountAccountInfoKeyspace_sample.csv'
PositionKeepingKeyspace_sample_out = '../MockData/Cassandra/PositionKeepingKeyspace/PositionKeepingKeyspace_sample.csv'
CustomerProfileKeyspaceCustomer_sample_out = '../MockData/Cassandra/CustomerProfileKeyspace/CustomerProfileKeyspace_sample.csv'
CustomerProfileKeyspaceAddress_sample_out = '../MockData/Cassandra/CustomerProfileKeyspace/CustomerProfileAddressKeyspace_sample.csv'

### Test de carga CustomerProfileCollection

In [8]:
#Carga de la información de dataframes por entidades
CustomerProfileCollection_df = pd.read_csv(CustomerProfileKeyspaceCustomer_sample_out) #Carga Sample
Address_df = pd.read_csv(CustomerProfileKeyspaceAddress_sample_out) #Carga Sample

#CustomerProfileCollection_df = pd.read_json(CustomerProfileCollection_file_out) 
#CurrentAccountCollection_df = pd.read_json(CurrentAccountCollection_file_out) 
#PositionKeepingCollection_df = pd.read_json(PositionKeepingCollection_file_out) 

In [9]:
print("CustomerProfileCollection_df",len(CustomerProfileCollection_df))
print("Address_df",len(Address_df))

CustomerProfileCollection_df 1000
Address_df 1000


In [10]:
for x in range(17): # Generamos un millon de registros aprox
    CustomerProfileCollection_df = CustomerProfileCollection_df.append(CustomerProfileCollection_df.sample(frac=0.60,replace = True))

for x in range(17):
    Address_df = Address_df.append(Address_df.sample(frac=0.60,replace = True))


In [11]:
print(len(CustomerProfileCollection_df))
print(len(Address_df))

2951634
2951634


In [12]:
num_documentos = 1000000

In [13]:
CustomerProfileCollection_df = CustomerProfileCollection_df.sample(num_documentos)
print(len(CustomerProfileCollection_df))
CustomerProfileCollection_df.sample(1)

1000000


PartyId  PartyNumber PartyType      Name FullLegalName LegalStructure  \
645     2534         2534       pri  Eleanore      Sam Hahn            Mr.   

     BeneficialOwnership        AccountRole        EmailAddress         Phone  
645                    2  US.OBIE.Principal  lera75@example.net  684-672-7207

In [14]:
Address_df = Address_df.sample(num_documentos)
print(len(Address_df))
Address_df.sample(1)

1000000


PartyId AddressType                      AddressLine         StreetName  \
709  1036194        Lake  74873 Bosco Junctions Suite 925  Armstrong Islands   

     BuildingNumber    PostCode          TownName  CountrySubDivision  \
709            1816  27442-6580  Lake Delphahaven           2544901.0   

     CountryId Country_Code Country_ShortName  \
709          2          SPA         Greatbrit   

                                   Country_Description  
709  Aut sapiente dicta illo consectetur nulla labo...

In [15]:
sample_mode = True #En cargas masivas reales, poner a false

if(sample_mode):
    list_partyId = CustomerProfileCollection_df['PartyId'].map(lambda x: str(uuid.uuid1()))
    CustomerProfileCollection_df['PartyId'] = list_partyId

In [16]:
CustomerProfileCollection_df.sample(5)

PartyId  PartyNumber PartyType      Name  \
387  e288b85a-bdd0-11ec-b9d9-cfb8fe60dbb7         1063       pri    Kamren   
219  e27c932c-bdd0-11ec-b9d9-cfb8fe60dbb7         5436       pri  Marielle   
324  e2f3bc40-bdd0-11ec-b9d9-cfb8fe60dbb7         3097       sol     Edwin   
892  e3491604-bdd0-11ec-b9d9-cfb8fe60dbb7         4322       sol   Ronaldo   
73   e3170024-bdd0-11ec-b9d9-cfb8fe60dbb7         9447       sol    Gladys   

      FullLegalName LegalStructure  BeneficialOwnership        AccountRole  \
387       Dasia Rau            Ms.                    8  UK.OBIE.Secundary   
219  Misty Schulist            Dr.                    9  DE.OBIE.Principal   
324       Liza Mohr            Ms.                    8  UK.OBIE.Secundary   
892    Ozella Boyer          Prof.                    6  UK.OBIE.Secundary   
73    Nayeli Larkin            Ms.                    4  UK.OBIE.Principal   

                  EmailAddress         Phone  
387  mabel.reichel@example.com  892.742.2435  
219      beaulah13@example.net  1-553-122-50  
324         eric10@example.net  229-202-9471  
892     merle.dare@example.net  035.191.4453  
73           mconn@example.com  421.391.9565

In [18]:
del(Address_df['PartyId'])
Address_df.sample(5)

AddressType                   AddressLine        StreetName  \
615        West               3218 Berta Fall  Leanne Mountains   
548        Nort               916 Stehr Forge     Marjory Coves   
674        West  574 Spencer Station Apt. 555      Franco Walks   
799        Lake  355 America Prairie Apt. 146   Ramiro Parkways   
424        Lake              124 Hilpert Park    Joaquin Manors   

     BuildingNumber    PostCode          TownName  CountrySubDivision  \
615            4692       28630     Harrisborough                85.0   
548           17984  19151-8138     East Elsafurt            539928.0   
674            9734       53071          New Pink            175019.0   
799            3607       01912    South Ninaland          37864543.0   
424             312       32359  North Tessieside              4660.0   

     CountryId Country_Code Country_ShortName  \
615          2          GBP               USA   
548          1          IND             Spain   
674          2          GBP               USA   
799          1          GBP               USA   
424          1          SPA         Greatbrit   

                                   Country_Description  
615  Id dolorem a soluta harum iusto qui repellat. ...  
548  Omnis dolore id dicta consequatur sit omnis. E...  
674  Id dolorem a soluta harum iusto qui repellat. ...  
799  Id dolorem a soluta harum iusto qui repellat. ...  
424  Aut sapiente dicta illo consectetur nulla labo...

In [19]:
import random

def getRandomAddresList():
    address_list = []
    num_add = random.randint(1, 3)
    for i in range(1,num_add):        
        AddressSample = Address_df.sample(1);
        tuple_add = (
            str(AddressSample['AddressType']).replace("'",""),
            str(AddressSample['AddressLine']).replace("'",""),
            str(AddressSample['StreetName']).replace("'",""),
            str(AddressSample['TownName']).replace("'",""),
            str(AddressSample['BuildingNumber']).replace("'",""),
            str(AddressSample['PostCode']).replace("'",""),
            str(AddressSample['CountrySubDivision']).replace("'",""),
            str(AddressSample['Country_Code']).replace("'",""),
            str(AddressSample['Country_ShortName']).replace("'",""),
            str(AddressSample['Country_Description']).replace("'","")
        )
        print(tuple_add)
        address_list.append(tuple_add)    
        
    return address_list


In [20]:
from cassandra import ConsistencyLevel
from cassandra.query import SimpleStatement

registers = []

#Cargas Masiva con Many
def loadCollectionDataFrame(df,keyspace):
    session = cluster.connect(keyspace)
    BATCH_SIZE = 1000
    iter = 0;
    i = 1
    time_inicial = time.time()
    for h,item in df.iterrows(): 
        INSERT_STMT = """INSERT INTO CustomerProfile (partyid, partynumber, partytype, name, fulllegalname, legalstructure, beneficialownership, accountrole, emailaddress, phone, address) VALUES ('{}', '{}', '{}', '{}', '{}', '{}', '{}', '{}', '{}', '{}', {});""".format(
            item[0].replace("'",""),
            item[1],
            item[2].replace("'",""),
            item[3].replace("'",""),
            item[4].replace("'",""),
            item[5].replace("'",""),
            item[6],
            item[7].replace("'",""),
            item[8].replace("'",""),
            item[9].replace("'",""),
            getRandomAddresList()
        )
        query = SimpleStatement(INSERT_STMT, consistency_level=ConsistencyLevel.QUORUM)
        #print(query)
        session.execute(query)
        
                
        if(i % BATCH_SIZE == 0 and i > 0):
            ### FIN BATCH   
            time_final = time.time()           
            data_time_collection = round(time_final - time_inicial,3)
            used_cpu = psutil.cpu_percent()
            mem_used = psutil.virtual_memory().percent
            registers.append((iter,data_time_collection,used_cpu,mem_used))
            print("new register:", (iter,data_time_collection,used_cpu,mem_used))
            iter += BATCH_SIZE;
            time_inicial = time.time()
        i = i + 1
    return registers

In [26]:
session.execute('TRUNCATE CustomerProfile;')

In [21]:
registers = loadCollectionDataFrame(CustomerProfileCollection_df, 'customerprofilekeyspace')

('72    West\nName: AddressType, dtype: object', '72    2256 King Mountain Suite 979\nName: AddressLine, dtype: object', '72    Eloise Greens\nName: StreetName, dtype: object', '72    New Felixside\nName: TownName, dtype: object', '72    89850\nName: BuildingNumber, dtype: int64', '72    10059-3581\nName: PostCode, dtype: object', '72    259679510.0\nName: CountrySubDivision, dtype: float64', '72    GBP\nName: Country_Code, dtype: object', '72    USA\nName: Country_ShortName, dtype: object', '72    Id dolorem a soluta harum iusto qui repellat. ...\nName: Country_Description, dtype: object')
('107    West\nName: AddressType, dtype: object', '107    7415 Angelita Glens Apt. 075\nName: AddressLine, dtype: object', '107    Georgiana Crest\nName: StreetName, dtype: object', '107    South Florine\nName: TownName, dtype: object', '107    665\nName: BuildingNumber, dtype: int64', '107    27313\nName: PostCode, dtype: object', '107    62326.0\nName: CountrySubDivision, dtype: float64', '107    

('735    New\nName: AddressType, dtype: object', '735    6486 Michele Mews Apt. 821\nName: AddressLine, dtype: object', '735    Fritsch Wells\nName: StreetName, dtype: object', '735    West Dedrick\nName: TownName, dtype: object', '735    1777\nName: BuildingNumber, dtype: int64', '735    48370-5005\nName: PostCode, dtype: object', '735    32768386.0\nName: CountrySubDivision, dtype: float64', '735    GBP\nName: Country_Code, dtype: object', '735    USA\nName: Country_ShortName, dtype: object', '735    Id dolorem a soluta harum iusto qui repellat. ...\nName: Country_Description, dtype: object')
('750    Nort\nName: AddressType, dtype: object', '750    60642 Bogan Ways\nName: AddressLine, dtype: object', '750    Weber Crossing\nName: StreetName, dtype: object', '750    Port Lindsay\nName: TownName, dtype: object', '750    172\nName: BuildingNumber, dtype: int64', '750    28947-9114\nName: PostCode, dtype: object', '750   NaN\nName: CountrySubDivision, dtype: float64', '750    IND\nName:

('552    New\nName: AddressType, dtype: object', '552    97783 Von Rapid Suite 811\nName: AddressLine, dtype: object', '552    Flatley Gateway\nName: StreetName, dtype: object', '552    South Anna\nName: TownName, dtype: object', '552    426\nName: BuildingNumber, dtype: int64', '552    52911-2666\nName: PostCode, dtype: object', '552    5.0\nName: CountrySubDivision, dtype: float64', '552    IND\nName: Country_Code, dtype: object', '552    Spain\nName: Country_ShortName, dtype: object', '552    Omnis dolore id dicta consequatur sit omnis. E...\nName: Country_Description, dtype: object')
('600    Sout\nName: AddressType, dtype: object', '600    83420 Rico Fields\nName: AddressLine, dtype: object', '600    Maryjane Vista\nName: StreetName, dtype: object', '600    East Gailbury\nName: TownName, dtype: object', '600    71577\nName: BuildingNumber, dtype: int64', '600    12918\nName: PostCode, dtype: object', '600    3260878.0\nName: CountrySubDivision, dtype: float64', '600    IND\nName: 

('405    Lake\nName: AddressType, dtype: object', '405    5737 Miller Lights\nName: AddressLine, dtype: object', '405    Kuvalis Burgs\nName: StreetName, dtype: object', '405    Ankundingview\nName: TownName, dtype: object', '405    721\nName: BuildingNumber, dtype: int64', '405    02128\nName: PostCode, dtype: object', '405    210142.0\nName: CountrySubDivision, dtype: float64', '405    GBP\nName: Country_Code, dtype: object', '405    USA\nName: Country_ShortName, dtype: object', '405    Id dolorem a soluta harum iusto qui repellat. ...\nName: Country_Description, dtype: object')
('364    West\nName: AddressType, dtype: object', '364    7780 Ressie Points\nName: AddressLine, dtype: object', '364    Kelsi Knolls\nName: StreetName, dtype: object', '364    West Felicitychester\nName: TownName, dtype: object', '364    544\nName: BuildingNumber, dtype: int64', '364    30317-8812\nName: PostCode, dtype: object', '364    306.0\nName: CountrySubDivision, dtype: float64', '364    GBP\nName: Co

('841    Nort\nName: AddressType, dtype: object', '841    1945 Lakin Ranch Apt. 599\nName: AddressLine, dtype: object', '841    Tavares Shoals\nName: StreetName, dtype: object', '841    West Claraside\nName: TownName, dtype: object', '841    4192\nName: BuildingNumber, dtype: int64', '841    86775-5940\nName: PostCode, dtype: object', '841    5905056.0\nName: CountrySubDivision, dtype: float64', '841    GBP\nName: Country_Code, dtype: object', '841    USA\nName: Country_ShortName, dtype: object', '841    Id dolorem a soluta harum iusto qui repellat. ...\nName: Country_Description, dtype: object')
('601    New\nName: AddressType, dtype: object', '601    12979 Maximus Cove\nName: AddressLine, dtype: object', '601    Ortiz Trafficway\nName: StreetName, dtype: object', '601    Haskellburgh\nName: TownName, dtype: object', '601    706\nName: BuildingNumber, dtype: int64', '601    80046\nName: PostCode, dtype: object', '601    7993146.0\nName: CountrySubDivision, dtype: float64', '601    SPA

...

('236    Nort\nName: AddressType, dtype: object', '236    5074 Eddie Haven Apt. 644\nName: AddressLine, dtype: object', '236    Leannon Springs\nName: StreetName, dtype: object', '236    Lake Braulioville\nName: TownName, dtype: object', '236    137\nName: BuildingNumber, dtype: int64', '236    38674-4571\nName: PostCode, dtype: object', '236    83231017.0\nName: CountrySubDivision, dtype: float64', '236    SPA\nName: Country_Code, dtype: object', '236    Greatbrit\nName: Country_ShortName, dtype: object', '236    Aut sapiente dicta illo consectetur nulla labo...\nName: Country_Description, dtype: object')
('38    Nort\nName: AddressType, dtype: object', '38    352 Sim Heights\nName: AddressLine, dtype: object', '38    Abigail Prairie\nName: StreetName, dtype: object', '38    East Nellie\nName: TownName, dtype: object', '38    9440\nName: BuildingNumber, dtype: int64', '38    01223\nName: PostCode, dtype: object', '38    3.0\nName: CountrySubDivision, dtype: float64', '38    IND\nName:

('236    Nort\nName: AddressType, dtype: object', '236    5074 Eddie Haven Apt. 644\nName: AddressLine, dtype: object', '236    Leannon Springs\nName: StreetName, dtype: object', '236    Lake Braulioville\nName: TownName, dtype: object', '236    137\nName: BuildingNumber, dtype: int64', '236    38674-4571\nName: PostCode, dtype: object', '236    83231017.0\nName: CountrySubDivision, dtype: float64', '236    SPA\nName: Country_Code, dtype: object', '236    Greatbrit\nName: Country_ShortName, dtype: object', '236    Aut sapiente dicta illo consectetur nulla labo...\nName: Country_Description, dtype: object')
('613    Lake\nName: AddressType, dtype: object', '613    614 Ferry Mill Suite 854\nName: AddressLine, dtype: object', '613    Addie Burg\nName: StreetName, dtype: object', '613    Estefaniabury\nName: TownName, dtype: object', '613    7656\nName: BuildingNumber, dtype: int64', '613    44363\nName: PostCode, dtype: object', '613    290109923.0\nName: CountrySubDivision, dtype: float6

('708    Lake\nName: AddressType, dtype: object', '708    347 Julien Meadow\nName: AddressLine, dtype: object', '708    Enrique Prairie\nName: StreetName, dtype: object', '708    Uptonfort\nName: TownName, dtype: object', '708    2080\nName: BuildingNumber, dtype: int64', '708    13996-8931\nName: PostCode, dtype: object', '708    94527614.0\nName: CountrySubDivision, dtype: float64', '708    SPA\nName: Country_Code, dtype: object', '708    Greatbrit\nName: Country_ShortName, dtype: object', '708    Aut sapiente dicta illo consectetur nulla labo...\nName: Country_Description, dtype: object')
('694    Lake\nName: AddressType, dtype: object', '694    179 Chelsey Path Apt. 781\nName: AddressLine, dtype: object', '694    Rempel Coves\nName: StreetName, dtype: object', '694    Davistown\nName: TownName, dtype: object', '694    2976\nName: BuildingNumber, dtype: int64', '694    27531-6553\nName: PostCode, dtype: object', '694    2347594.0\nName: CountrySubDivision, dtype: float64', '694    S

('533    West\nName: AddressType, dtype: object', '533    6482 Micah Shore Apt. 981\nName: AddressLine, dtype: object', '533    Lakin Valley\nName: StreetName, dtype: object', '533    Port Burdettehaven\nName: TownName, dtype: object', '533    962\nName: BuildingNumber, dtype: int64', '533    82783\nName: PostCode, dtype: object', '533    43.0\nName: CountrySubDivision, dtype: float64', '533    IND\nName: Country_Code, dtype: object', '533    Spain\nName: Country_ShortName, dtype: object', '533    Omnis dolore id dicta consequatur sit omnis. E...\nName: Country_Description, dtype: object')
('781    Lake\nName: AddressType, dtype: object', '781    405 Gerson Trafficway Apt. 079\nName: AddressLine, dtype: object', '781    Tillman Villages\nName: StreetName, dtype: object', '781    Mortonburgh\nName: TownName, dtype: object', '781    3197\nName: BuildingNumber, dtype: int64', '781    03877\nName: PostCode, dtype: object', '781    171.0\nName: CountrySubDivision, dtype: float64', '781    I

KeyboardInterrupt: 

In [297]:
registers

[(0, 0.437, 11.2, 66.9),
 (100, 0.513, 26.0, 66.9),
 (200, 0.41, 22.5, 67.0),
 (300, 0.563, 18.5, 67.0),
 (400, 1.298, 25.6, 67.0),
 (500, 0.564, 19.6, 67.0),
 (600, 0.418, 19.5, 67.0),
 (700, 0.493, 24.2, 66.9),
 (800, 0.853, 25.2, 67.0),
 (900, 0.877, 21.1, 67.0)]

In [ ]:
save_results_to_csv(registers,resultados_etl_CutomerProfileKeySpace, 'QUORUM')